# <ins> Finalizing the boundary-setting </ins>
Based on the last three models, we managed to obtain a pretty solid mapping of the areas of Eindhoven which could properly fit the definitions provided by Fieke.
It is crucial now to define these boundaries as accurately as possible; the goal of this notebook is thus to see how we can overlay Alex and Sjoerd's findings to the current mappings, and extract a more detailed map with clearly defined boundaries.


## Overlaying the maps
First, as I mentioned, we need to overlay the final mapping of Eindhoven that I designed to the mapping provided by Alex and Sjoerd; this will give us the most accurate mapping of the zones we will be working with, and will allow us to properly model the points of connection we want to place later on.

Analyzing the map the Built Environment guys provided, you can see that **all of the regions fit inside the boundary-passing model zones!** This means that what we need to do at this point is to merge and fit the specific OSM boundaries we will use to these distinctions, and create a workable map where all of the regions are split in this manner. The most accurate manner of doing this would be to manually extract the polygons using GeoJSON or by using QGIS and referencing the two maps; I opted to use the first approach, since we then can easily re-shape the neighborhoods if new data is provided.

You can see the file containing these boundaries **refinedMap.geojson** in the same directory as this Python notebook; after loading using folium and geopandas, it looks as follows:




In [1]:
import geopandas as gpd
import osmnx as ox
import json
import folium
from IPython.display import display, HTML

with open("refinedMap.geojson") as openedFile:
    polygonGeoJSON = json.load(openedFile)

# Convert GeoJSON to GeoDataFrame
geoDataEindhoven = gpd.GeoDataFrame.from_features(polygonGeoJSON["features"])
polygon = geoDataEindhoven.geometry.values[0]

# Create a Folium map centered on Eindhoven
eindhoven_map = folium.Map(location=[51.4416, 5.4697], zoom_start=12, tiles="cartodbpositron")

# Add the GeoJSON data to the map
folium.GeoJson(
    polygonGeoJSON,
    name="Eindhoven Boundaries",
    style_function=lambda feature: {
        "fillColor": "blue",
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.5,
    },
).add_to(eindhoven_map)
display(HTML(eindhoven_map._repr_html_()))

Now, we convert the GeoJSON data that I plotted into a working polygon, so that we may use it with OSMNx for optimal point plotting.

In [2]:
import geopandas as gpd
import pandas as pd
import osmnx as ox
import json

with open("refinedMap.geojson") as openedFile:
    polygonGeoJSON = json.load(openedFile)
    
geoDataEindhoven = gpd.GeoDataFrame.from_features(polygonGeoJSON["features"])
polygon = geoDataEindhoven.geometry.values[0]


Everything's converted - we can move on to finding the points we will use for our hubs.

## Finding low-efficiency zones

I am still brainstorming if there is a better way of going about this, but for now, the best approach would be to do what we presented in the midterm presentation: highlighting low-scoring zones in terms of 15-minute walkability, and then further refining where within these zones it would be best to place the bikes.

In [3]:
from shapely.geometry import Point, Polygon
import numpy as npo
import folium

with open("refinedMap.geojson") as openedFile:
    polygonGeoJSON = json.load(openedFile)

geoDataEindhoven = gpd.GeoDataFrame.from_features(polygonGeoJSON["features"])
polygons = geoDataEindhoven.geometry

# I use the same tags I used before, since we agreed on them as a form of baseline, and the map Sjoerd showed used very
# similar tags. I added a few things to the "leisure" and "shop" tags because I realized that they are not as varied
# as the "office" and "amenity" tags. 

tags = {
    'office': ['yes'],  # All workplaces, since OSM has an incredible amount of identifiers.
    'shop': ['supermarket', 'convenience', 'bakery', 'greengrocer', 'butcher'],
    'amenity': [
        'pharmacy', 'hospital', 'clinic', 'doctors', 
        'school', 'kindergarten', 'college', 'university',  
        'cafe', 'restaurant', 'bar', 'cinema', 'theatre',  
        'community_centre', 'library', 'bicycle_rental',
        'place_of_worship'
        # Place of worship can be considered "key" ammenity for some, so should be included.
    ],
    'leisure': [
        'park', 'fitness_centre', 'sports_centre', 'stadium', 
        'dog_park', 'pitch', 'swimming_pool', 'playground',
        'nature_reserve'
    ],
    'shop' : [
        'supermarket', 'convenience', 'bakery', 'greengrocer', 'butcher',
        'department_store', 'general', 'cosmetics', 'stationery'
    ]
}

# First, we generate a grid of poinst so that this may actually be treated as a graphing problem.
def generateGrid(polygon, spacing=0.0015):
    minx, miny, maxx, maxy = polygon.bounds
    x_coords = npo.arange(minx, maxx, spacing)
    y_coords = npo.arange(miny, maxy, spacing)
    points = [Point(x,y) for x in x_coords for y in y_coords if polygon.contains(Point(x,y))]
    return points

# Then, we may simply analyze the polygons the same way we did way back in the original simulations,
# and give each polygon a score according to its accessibility.
lowScoreZones = []
for polygon in polygons:
    # As usual, needs some debugging messages
    print("Processing a new polygon... as always, might take a while.")
    
    # Generate a grid of points within the polygon - this is based on size of polygon, so 
    # there are obviously more points in larger polygons. Smallest ones has ~15, largest ~67
    grid_points = generateGrid(polygon)
    print(f"Generated {len(grid_points)} grid points within the polygon.")
    
    # Query OSM for the specified tags
    amenities = ox.features_from_polygon(polygon, tags)
    print(f"Found {len(amenities)} amenities in the polygon.")
    
    # Check accessibility for each grid point
    lowScoringPoints = []
    amenityCountsPer = []
    
    for point in grid_points:
        # Create a 15-minute walking isochrone (approximately 1.2 km radius)
        isochrone = point.buffer(0.012)  # 1.2 km in degrees
        
        # Check if the isochrone contains any amenities
        accessible_amenities = amenities[amenities.intersects(isochrone)]
        amenityCount = len(accessible_amenities)
        amenityCountsPer.append(amenityCount)
        
    # The rubric used by CityAccessMap scores the "Average" zones to be below 50% of the max;
    # here, I use 30%.
    maxAm = max(amenityCountsPer) if amenityCountsPer else 0
    threshold = maxAm * 0.5
    
    for point, count in zip(grid_points, amenityCountsPer):
        if count < threshold:
            lowScoringPoints.append(point)
    
    print(f"Identified {len(lowScoringPoints)} low-scoring points in the polygon.")
    lowScoreZones.append(gpd.GeoDataFrame(geometry=lowScoringPoints))
    
# Now, we need to visualize this! 
# We do what we did earlier, and convert to a single GeoDataFrame.
lowScoreZonesGDF = gpd.GeoDataFrame(pd.concat(lowScoreZones, ignore_index=True))
eindhoven_map = folium.Map(location=[51.4416, 5.4697], zoom_start=12, tiles="cartodbpositron")

# Add the low-scoring points to the map
for _, row in lowScoreZonesGDF.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=4,  # Slightly larger radius for low-scoring points
        color="red",  # Red color for low-scoring points
        fill=True,
        fill_opacity=0.8,
    ).add_to(eindhoven_map)

# Add the generated grid points to the map
for polygon in polygons:
    # Generate a grid of points within the polygon
    grid_points = generateGrid(polygon)
    
    # Add each grid point to the map
    for point in grid_points:
        folium.CircleMarker(
            location=[point.y, point.x],
            radius=2,  # Smaller radius for grid points
            color="green",  # Green color for grid points
            fill=True,
            fill_opacity=0.6,
        ).add_to(eindhoven_map)

# Query OSM for bus stops within the Eindhoven boundary
bus_stop_tag = {'highway': 'bus_stop'}
bus_stops = ox.features_from_polygon(polygons.unary_union, bus_stop_tag)  # Combine all polygons into one

# Debugging: Print the number of bus stops found
print(f"Found {len(bus_stops)} bus stops in Eindhoven.")

# Add bus stops to the map
for _, bus_stop in bus_stops.iterrows():
    if bus_stop.geometry.geom_type == 'Point':  # Ensure the geometry is a point
        folium.CircleMarker(
            location=[bus_stop.geometry.y, bus_stop.geometry.x],
            radius=3,  # Smaller radius for bus stops
            color="blue",  # Blue color for bus stops
            fill=True,
            fill_opacity=0.8,
            tooltip="Bus Stop",  # Optional: Add a tooltip
        ).add_to(eindhoven_map)

# Add the original polygons
folium.GeoJson(
    polygonGeoJSON,
    name="Eindhoven Boundaries",
    style_function=lambda feature: {
        "fillColor": "blue",
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.2,
    },
).add_to(eindhoven_map)

# Save the map (for sharing)
output_file = "eindhoven_map_with_bus_stops.html"
eindhoven_map.save(output_file)
print(f'Map saved to {output_file}')

# Display the map
eindhoven_map

Processing a new polygon... as always, might take a while.
Generated 640 grid points within the polygon.
Found 358 amenities in the polygon.
Identified 198 low-scoring points in the polygon.
Processing a new polygon... as always, might take a while.
Generated 499 grid points within the polygon.
Found 572 amenities in the polygon.
Identified 283 low-scoring points in the polygon.
Processing a new polygon... as always, might take a while.
Generated 229 grid points within the polygon.
Found 103 amenities in the polygon.
Identified 32 low-scoring points in the polygon.
Processing a new polygon... as always, might take a while.
Generated 254 grid points within the polygon.
Found 172 amenities in the polygon.
Identified 27 low-scoring points in the polygon.
Processing a new polygon... as always, might take a while.
Generated 183 grid points within the polygon.
Found 68 amenities in the polygon.
Identified 31 low-scoring points in the polygon.


C:\Users\euseb\AppData\Local\Temp\ipykernel_18068\464915959.py:118: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  bus_stops = ox.features_from_polygon(polygons.unary_union, bus_stop_tag)  # Combine all polygons into one


Found 275 bus stops in Eindhoven.
Map saved to eindhoven_map_with_bus_stops.html


## Mapping the improvement zones.
Looking at the map displayed above, we can see clearly see a number of zones which acommodate access to fewer services than is the average for the rest of the city. We specifically use this criterium for measurement, since we have already checked for 15-minute accessibility, alongside optimal population density and service diversity; the goal now is to "even out" these zones which do not adhere to a city-wide standard of mobility.

Sjoerd and Alex found a number of suitable locations which may be used for the placement of mobility hubs around the city. I overlaid these maps to obtain a provisional selection, manually mapping the potential zones of placement in accordance with existing infrastructure that I found on Google Maps. Some explanations are in order to fully explain the mapping of these locations:

1) To make our project future-proof, we decided to plan with the transformations to the Eindhoven Station Area in mind, specifically adhering to the planned modifications to the Eindhoven Central station as planned by KCAP. Although the placement of the hub in a zone of high-mobility may initially seem counterintuitive, after deliberation we have concluded that such an incusion would seamlessly integrate with the existing transport infrastructure and allow for further access to other mobility hubs.

2) The specific placement of the hubs as *physical* spaces is done as follows:
- Where possible 
- Where possible, the zones are incorporated into preexisting infrastructure, replacing vacant lots where possible, and where this is impossible, being composed into existing car-centric infrastructure, such as parking lots.
- If the above is not possible, the zones are extended to give planners an array of potential locations which can still be modeled appropriately

    In general, the zones are mapped in a manner such that they can be abstracted to a single point consistent with the grid used for previous mapping.

Some more comments regarding specific zones:
1) Mercuriuslaan zone: fitted into a pre-existing green space.
2) Catharina Ziekhuis / Maxima Medisch Centrum / Anna Ziekhuis: accessibility of the disabled
3) Catharina Ziekhuis: big transit point.
3) Next to Stroomz de Akkers: playground
4) Lavendelstraat: tight area with slight expansion and green zone.
5) Solmsweg: vacant lot between two apartment blocks; cant use other one

You may see the zones in the Folium map provided below: they are highlighted in a XXX color so that they may be more distinctly recognized. In the next step, we will try to see how these may improve communication to acquire an estimate of their sustainability.

In [4]:
with open("hubLocations.geojson") as hubMapFile:
    hubPolygon = json.load(hubMapFile)

# As with the full Eindhoven map, we convert the GeoJSON to a GeoDataFrame:
hubGeoDataFrame = gpd.GeoDataFrame.from_features(hubPolygon["features"])
polygon = hubGeoDataFrame.geometry.values[0]

# Create a Folium map centered on the hub locations drawn in GeoJSON:
hubMapEindhoven = folium.Map(location=[51.4416, 5.4697], zoom_start=12, tiles="cartodbpositron")

# We want to highlight the placements of the mobility hubs, so we specify their coordinate points as
# geojson features. This was A PAIN to write down, since gejson formatting is finicky.
hubCoordinates = [
    [
        [5.479242878818951, 51.44325775636963],
        [5.4776044181902535, 51.443029567735266],
        [5.478054544736551, 51.44202702055455],
        [5.479500951372074, 51.442210323735026],
        [5.479242878818951, 51.44325775636963]
    ],
    [
        [5.4705474804922005, 51.46453387794932],
        [5.4705542616922, 51.46434165458419],
        [5.471249334683762, 51.464352216328365],
        [5.471235772283819, 51.4644599459815],
        [5.473435691022786, 51.46451142198288],
        [5.473427854871261, 51.464868533654055],
        [5.47064438961209, 51.46480740637557],
        [5.470659881996994, 51.46454037572332],
        [5.4705474804922005, 51.46453387794932]
    ],
    [
        [5.4909987501103785, 51.47036299334738],
        [5.490919511068853, 51.46992304756114],
        [5.491994405882707, 51.469843642259804],
        [5.4920529738699315, 51.47017628516602],
        [5.492080535274624, 51.4702921730929],
        [5.4909987501103785, 51.47036299334738]
    ],
    [
        [5.488958986867033, 51.454195789565574],
        [5.488928429428, 51.453770525969844],
        [5.489634645789067, 51.45373455822033],
        [5.4896719937700595, 51.454187326647],
        [5.489675389041054, 51.45432696460165],
        [5.489230608544062, 51.45433754321695],
        [5.489217027460029, 51.45420848394019],
        [5.488958986867033, 51.454195789565574]
    ],
    [
        [5.474621202205924, 51.47619067373631],
        [5.474591931246323, 51.4758989748988],
        [5.475477377799393, 51.475871628037254],
        [5.475506648758994, 51.476181558175796],
        [5.474621202205924, 51.47619067373631]
    ],
    [
        [5.520386704860698, 51.439007813779085],
        [5.519824170435442, 51.438839165418216],
        [5.519984894556927, 51.438605394382506],
        [5.5204617094507, 51.43868554458689],
        [5.520560822659149, 51.438752336315815],
        [5.520386704860698, 51.439007813779085]
    ],
    [
        [5.488345696419913, 51.420028453490715],
        [5.488251180343866, 51.419494880781485],
        [5.490116629225724, 51.41935218004775],
        [5.4902260688930085, 51.41989506089749],
        [5.489972367845638, 51.41999432984127],
        [5.488644168240938, 51.42009670071329],
        [5.488345696419913, 51.420028453490715]
    ],
    [
        [5.501149290906795, 51.4223639138599],
        [5.5009076675460165, 51.42221998989163],
        [5.501679419772273, 51.42169151518314],
        [5.502678370083771, 51.42225597092616],
        [5.50241510881105, 51.42239989478114],
        [5.501765971424646, 51.42195912654381],
        [5.501149290906795, 51.4223639138599]
    ],
    [
        [5.460946434395254, 51.43035395528261],
        [5.4604985090147125, 51.42993147397817],
        [5.461210595517542, 51.42960207906458],
        [5.461662349320193, 51.42941828521862],
        [5.462412720042806, 51.430081849127504],
        [5.462064333635595, 51.43021074171892],
        [5.461788687248202, 51.429991146715935],
        [5.460946434395254, 51.43035395528261]
    ],
    [
        [5.444885035992172, 51.42007169912026],
        [5.44524278164252, 51.41910093602877],
        [5.4476986571833095, 51.420324938274774],
        [5.447398924341599, 51.4205480287485],
        [5.446345024994912, 51.42024052537914],
        [5.44554251448281, 51.42013802379617],
        [5.444885035992172, 51.42007169912026]
    ]
]

# Method for checking if a feature is a mobility hub zone:
# used later in the Folium map to style the hub locations.
def isHub(feature):
    coordinates = feature["geometry"]["coordinates"][0]
    return coordinates in hubCoordinates

# Add the hub locations to the map
folium.GeoJson(
    hubPolygon,
    name="Hub Locations",
    style_function=lambda feature: {
        "fillColor": "red" if isHub(feature) else "blue", 
        "color": "black",
        "weight": 1,
        "fillOpacity": 0.5 if isHub(feature) else 0.2,
    },
).add_to(hubMapEindhoven)
display(HTML(hubMapEindhoven._repr_html_()))

## Measuring improvement and eliminating inefficiencies
Our goal in this part of the modelling assignment is to adjust the placement of the zones such that the efficiency of their placement is maximal. We thus need to define two things for the process of elimination that is to follow: the scoring method and the goal.

1) **Scoring method**: in our development of the original map, we measured the suitability of a point on the overlaid grid to fit a 15-minute city by measuring its adherence to the walkability-standard of the city (as measured by the density of services.) To align with this, we make each mobility hub zone an "upgrade" to the grid it overlays: each point within the 15-minute walking radius of a hub has its "accessibility" radius expanded by the size that can be covered within 15 minutes by biking (minus the time spent walking.) This allows for a solid model of how each zone improves the area around it (though one still recquiring solid simulation)

2) **Goal**: as the name of the category implies, this is an "elimination process": after running the model, we will highlight the zones which improve accessibility by the highest margin (as measured by the overall increase in service density from the points affected by the hub placement), and extract them for our later simulation.

We begin by first overlaying the grid onto the map, as we did during our primary simulation:

In [5]:
# Load Eindhoven polygon GeoJSON
with open("refinedMap.geojson") as openedFile:
    polygonGeoJSON = json.load(openedFile)

geoDataEindhoven = gpd.GeoDataFrame.from_features(polygonGeoJSON["features"])
polygons = geoDataEindhoven.geometry

# Weird Jupyter notebook issue: I can reuse tags no problem, same with a number of variables,
# but if I try to reuse the hubCoordinates variable, it only uses a selection of them.
# So, I just copy-paste the hub coordinates here again.

hubCoordinates = [
    [
        [5.479242878818951, 51.44325775636963],
        [5.4776044181902535, 51.443029567735266],
        [5.478054544736551, 51.44202702055455],
        [5.479500951372074, 51.442210323735026],
        [5.479242878818951, 51.44325775636963]
    ],
    [
        [5.4705474804922005, 51.46453387794932],
        [5.4705542616922, 51.46434165458419],
        [5.471249334683762, 51.464352216328365],
        [5.471235772283819, 51.4644599459815],
        [5.473435691022786, 51.46451142198288],
        [5.473427854871261, 51.464868533654055],
        [5.47064438961209, 51.46480740637557],
        [5.470659881996994, 51.46454037572332],
        [5.4705474804922005, 51.46453387794932]
    ],
    [
        [5.4909987501103785, 51.47036299334738],
        [5.490919511068853, 51.46992304756114],
        [5.491994405882707, 51.469843642259804],
        [5.4920529738699315, 51.47017628516602],
        [5.492080535274624, 51.4702921730929],
        [5.4909987501103785, 51.47036299334738]
    ],
    [
        [5.488958986867033, 51.454195789565574],
        [5.488928429428, 51.453770525969844],
        [5.489634645789067, 51.45373455822033],
        [5.4896719937700595, 51.454187326647],
        [5.489675389041054, 51.45432696460165],
        [5.489230608544062, 51.45433754321695],
        [5.489217027460029, 51.45420848394019],
        [5.488958986867033, 51.454195789565574]
    ],
    [
        [5.474621202205924, 51.47619067373631],
        [5.474591931246323, 51.4758989748988],
        [5.475477377799393, 51.475871628037254],
        [5.475506648758994, 51.476181558175796],
        [5.474621202205924, 51.47619067373631]
    ],
    [
        [5.520386704860698, 51.439007813779085],
        [5.519824170435442, 51.438839165418216],
        [5.519984894556927, 51.438605394382506],
        [5.5204617094507, 51.43868554458689],
        [5.520560822659149, 51.438752336315815],
        [5.520386704860698, 51.439007813779085]
    ],
    [
        [5.488345696419913, 51.420028453490715],
        [5.488251180343866, 51.419494880781485],
        [5.490116629225724, 51.41935218004775],
        [5.4902260688930085, 51.41989506089749],
        [5.489972367845638, 51.41999432984127],
        [5.488644168240938, 51.42009670071329],
        [5.488345696419913, 51.420028453490715]
    ],
    [
        [5.501149290906795, 51.4223639138599],
        [5.5009076675460165, 51.42221998989163],
        [5.501679419772273, 51.42169151518314],
        [5.502678370083771, 51.42225597092616],
        [5.50241510881105, 51.42239989478114],
        [5.501765971424646, 51.42195912654381],
        [5.501149290906795, 51.4223639138599]
    ],
    [
        [5.460946434395254, 51.43035395528261],
        [5.4604985090147125, 51.42993147397817],
        [5.461210595517542, 51.42960207906458],
        [5.461662349320193, 51.42941828521862],
        [5.462412720042806, 51.430081849127504],
        [5.462064333635595, 51.43021074171892],
        [5.461788687248202, 51.429991146715935],
        [5.460946434395254, 51.43035395528261]
    ],
    [
        [5.444885035992172, 51.42007169912026],
        [5.44524278164252, 51.41910093602877],
        [5.4476986571833095, 51.420324938274774],
        [5.447398924341599, 51.4205480287485],
        [5.446345024994912, 51.42024052537914],
        [5.44554251448281, 51.42013802379617],
        [5.444885035992172, 51.42007169912026]
    ]
]

# This is the crux of this entire modification - instead of measuring via point-to-point
# of the boundaries defined in hubCoordinates, we create a Polygon object for each hub.

hub_polygons = [Polygon(hub) for hub in hubCoordinates]

# Check proximity to any hub (using the centroid of the hub polygons)
# I don't know if I ever explained what a centroid is so - essentially, a geometrical feature's center of gravity.
def within_hub_proximity(point, hubs, threshold_m=500):
    threshold_deg = threshold_m / 111320  # Approximate conversion: 1 deg ≈ 111.32 km
    for hub in hubs:
        if point.distance(hub.centroid) <= threshold_deg:
            return True
    return False

# Main accessibility analysis
accessible_points = []
inaccessible_points = []

for polygon in polygons:
    grid_points = generateGrid(polygon)
    amenities = ox.features_from_polygon(polygon, tags)

    for point in grid_points:
        radius = 0.1 if within_hub_proximity(point, hub_polygons) else 0.012
        isochrone = point.buffer(radius)
        accessible_amenities = amenities[amenities.intersects(isochrone)]
        if len(accessible_amenities) >= 10:
            accessible_points.append(point)
        else:
            inaccessible_points.append(point)

# Convert lowScoreZones to a set for faster lookup
low_score_points = set(pt for zone in lowScoreZones for pt in zone.geometry)

# Visualization
eindhoven_map = folium.Map(location=[51.4416, 5.4697], zoom_start=12, tiles="cartodbpositron")

# Add polygons
folium.GeoJson(polygonGeoJSON).add_to(eindhoven_map)

# Add mobility hubs (red color)
for poly in hub_polygons:
    folium.Polygon(
        locations=[(pt[1], pt[0]) for pt in poly.exterior.coords],
        color='red', weight=2, fill=True, fill_opacity=0.3
    ).add_to(eindhoven_map)

# Add accessible (green) and inaccessible (red) points
for pt in accessible_points:
    # Check if the point was previously in lowScoreZones
    if pt in low_score_points:
        # Highlight improvement nodes in orange
        folium.CircleMarker(
            location=[pt.y, pt.x], radius=2, color="darkgreen", fill=True, fill_opacity=0.6
        ).add_to(eindhoven_map)
    else:
        # Regular accessible points in green
        folium.CircleMarker(
            location=[pt.y, pt.x], radius=2, color="green", fill=True, fill_opacity=0.6
        ).add_to(eindhoven_map)

# Add inaccessible points (still in lowScoreZones)
for pt in low_score_points:
    if pt not in accessible_points:  # Ensure these points are still inaccessible
        folium.CircleMarker(
            location=[pt.y, pt.x], radius=2, color="red", fill=True, fill_opacity=0.6
        ).add_to(eindhoven_map)

# Save the map
eindhoven_map


## Measuring improvement and eliminating inefficiencies
Our goal in this part of the modelling assignment is to adjust the placement of the zones such that the efficiency of their placement is maximal. We thus need to define two things for the process of elimination that is to follow: the scoring method and the goal.

1) **Scoring method**: in our development of the original map, we measured the suitability of a point on the overlaid grid to fit a 15-minute city by measuring its adherence to the walkability-standard of the city (as measured by the density of services.) To align with this, we make each mobility hub zone an "upgrade" to the grid it overlays: each point within the 15-minute walking radius of a hub has its "accessibility" radius expanded by the size that can be covered within 15 minutes by biking (minus the time spent walking.) This allows for a solid model of how each zone improves the area around it (though one still recquiring solid simulation)

2) **Goal**: as the name of the category implies, this is an "elimination process": after running the model, we will highlight the zones which improve accessibility by the highest margin (as measured by the overall increase in service density from the points affected by the hub placement), and extract them for our later simulation.

We begin by first overlaying the grid onto the map, as we did during our primary simulation:

In [6]:
# Load Eindhoven polygon GeoJSON
with open("refinedMap.geojson") as openedFile:
    polygonGeoJSON = json.load(openedFile)

geoDataEindhoven = gpd.GeoDataFrame.from_features(polygonGeoJSON["features"])
polygons = geoDataEindhoven.geometry

# Weird Jupyter notebook issue: I can reuse tags no problem, same with a number of variables,
# but if I try to reuse the hubCoordinates variable, it only uses a selection of them.
# So, I just copy-paste the hub coordinates here again.

hubCoordinates = [
    [
        [5.479242878818951, 51.44325775636963],
        [5.4776044181902535, 51.443029567735266],
        [5.478054544736551, 51.44202702055455],
        [5.479500951372074, 51.442210323735026],
        [5.479242878818951, 51.44325775636963]
    ],
    [
        [5.4705474804922005, 51.46453387794932],
        [5.4705542616922, 51.46434165458419],
        [5.471249334683762, 51.464352216328365],
        [5.471235772283819, 51.4644599459815],
        [5.473435691022786, 51.46451142198288],
        [5.473427854871261, 51.464868533654055],
        [5.47064438961209, 51.46480740637557],
        [5.470659881996994, 51.46454037572332],
        [5.4705474804922005, 51.46453387794932]
    ],
    # [
    #     [5.4909987501103785, 51.47036299334738],
    #     [5.490919511068853, 51.46992304756114],
    #     [5.491994405882707, 51.469843642259804],
    #     [5.4920529738699315, 51.47017628516602],
    #     [5.492080535274624, 51.4702921730929],
    #     [5.4909987501103785, 51.47036299334738]
    # ],
    # Catharina Hospital - kind of needed.
    [
        [5.488958986867033, 51.454195789565574],
        [5.488928429428, 51.453770525969844],
        [5.489634645789067, 51.45373455822033],
        [5.4896719937700595, 51.454187326647],
        [5.489675389041054, 51.45432696460165],
        [5.489230608544062, 51.45433754321695],
        [5.489217027460029, 51.45420848394019],
        [5.488958986867033, 51.454195789565574]
    ],
    [
        [5.474621202205924, 51.47619067373631],
        [5.474591931246323, 51.4758989748988],
        [5.475477377799393, 51.475871628037254],
        [5.475506648758994, 51.476181558175796],
        [5.474621202205924, 51.47619067373631]
    ],
    [
        [5.520386704860698, 51.439007813779085],
        [5.519824170435442, 51.438839165418216],
        [5.519984894556927, 51.438605394382506],
        [5.5204617094507, 51.43868554458689],
        [5.520560822659149, 51.438752336315815],
        [5.520386704860698, 51.439007813779085]
    ],
    [
        [5.488345696419913, 51.420028453490715],
        [5.488251180343866, 51.419494880781485],
        [5.490116629225724, 51.41935218004775],
        [5.4902260688930085, 51.41989506089749],
        [5.489972367845638, 51.41999432984127],
        [5.488644168240938, 51.42009670071329],
        [5.488345696419913, 51.420028453490715]
    ],
    # Small mobility hub squeezed in-between two tight roads - I'm very keen on removing this one.
    # [
    #     [5.501149290906795, 51.4223639138599],
    #     [5.5009076675460165, 51.42221998989163],
    #     [5.501679419772273, 51.42169151518314],
    #     [5.502678370083771, 51.42225597092616],
    #     [5.50241510881105, 51.42239989478114],
    #     [5.501765971424646, 51.42195912654381],
    #     [5.501149290906795, 51.4223639138599]
    # ],
    # Border mobility hub right next to the central district and on the edge of the southern one.
    # [
    #     [5.460946434395254, 51.43035395528261],
    #     [5.4604985090147125, 51.42993147397817],
    #     [5.461210595517542, 51.42960207906458],
    #     [5.461662349320193, 51.42941828521862],
    #     [5.462412720042806, 51.430081849127504],
    #     [5.462064333635595, 51.43021074171892],
    #     [5.461788687248202, 51.429991146715935],
    #     [5.460946434395254, 51.43035395528261]
    # ],
    # West-most Southern mobility hub  - central to that whole region, so I'm not keen on moving it.
    [
        [5.444885035992172, 51.42007169912026],
        [5.44524278164252, 51.41910093602877],
        [5.4476986571833095, 51.420324938274774],
        [5.447398924341599, 51.4205480287485],
        [5.446345024994912, 51.42024052537914],
        [5.44554251448281, 51.42013802379617],
        [5.444885035992172, 51.42007169912026]
    ]
]

# This is the crux of this entire modification - instead of measuring via point-to-point
# of the boundaries defined in hubCoordinates, we create a Polygon object for each hub.

hub_polygons = [Polygon(hub) for hub in hubCoordinates]

# Check proximity to any hub (using the centroid of the hub polygons)
# I don't know if I ever explained what a centroid is so - essentially, a geometrical feature's center of gravity.
def within_hub_proximity(point, hubs, threshold_m=500):
    threshold_deg = threshold_m / 111320  # Approximate conversion: 1 deg ≈ 111.32 km
    for hub in hubs:
        if point.distance(hub.centroid) <= threshold_deg:
            return True
    return False

# Main accessibility analysis
accessible_points = []
inaccessible_points = []

for polygon in polygons:
    grid_points = generateGrid(polygon)
    amenities = ox.features_from_polygon(polygon, tags)

    for point in grid_points:
        radius = 0.05 if within_hub_proximity(point, hub_polygons) else 0.012
        isochrone = point.buffer(radius)
        accessible_amenities = amenities[amenities.intersects(isochrone)]
        if len(accessible_amenities) >= 10:
            accessible_points.append(point)
        else:
            inaccessible_points.append(point)

# Convert lowScoreZones to a set for faster lookup
low_score_points = set(pt for zone in lowScoreZones for pt in zone.geometry)

# Visualization
eindhoven_map = folium.Map(location=[51.4416, 5.4697], zoom_start=12, tiles="cartodbpositron")

# Add polygons
folium.GeoJson(polygonGeoJSON).add_to(eindhoven_map)

# Add mobility hubs (red color)
for poly in hub_polygons:
    folium.Polygon(
        locations=[(pt[1], pt[0]) for pt in poly.exterior.coords],
        color='red', weight=2, fill=True, fill_opacity=0.3
    ).add_to(eindhoven_map)

# Add accessible (green) and inaccessible (red) points
for pt in accessible_points:
    # Check if the point was previously in lowScoreZones
    if pt in low_score_points:
        # Highlight improvement nodes in orange
        folium.CircleMarker(
            location=[pt.y, pt.x], radius=2, color="darkgreen", fill=True, fill_opacity=0.6
        ).add_to(eindhoven_map)
    else:
        # Regular accessible points in green
        folium.CircleMarker(
            location=[pt.y, pt.x], radius=2, color="green", fill=True, fill_opacity=0.6
        ).add_to(eindhoven_map)

# Add inaccessible points (still in lowScoreZones)
for pt in low_score_points:
    if pt not in accessible_points:  # Ensure these points are still inaccessible
        folium.CircleMarker(
            location=[pt.y, pt.x], radius=2, color="red", fill=True, fill_opacity=0.6
        ).add_to(eindhoven_map)

# Save the map
eindhoven_map


## Adapting for simulation
All we need to do to convert the visualizations above to actual data points which we can use for real time simulation, is to measure how close our mobility hubs are to actual graph points present on the OSM Eindhoven map. With these points, we will be able to run a shortest path algorithm to motivate their existance. 

In [7]:
import agent as ag
import pandas as pd
import geopandas as gpd

hub_polygons = [Polygon(hub) for hub in hubCoordinates]

# Get the data from agent.dists
data, all_pairs_distances = ag.dists.initialize()
graph = data["graph"]

# Create new features for hubs
def create_hub_features(hubs):
    hub_features = []
    for i, hub in enumerate(hubs):
        nearest_node = ox.distance.nearest_nodes(graph, hub.centroid.x, hub.centroid.y)
        centroid = hub.centroid
        hub_features.append({
            "id": f"hub_{i}",
            "geometry": centroid,
            "main_tag": "hub",
            "centroid": centroid,
            "nearest_node": nearest_node
        })
    return hub_features

# Create hub features
hub_features = create_hub_features(hub_polygons)

# Add hub features to data
ag.dists.features = pd.concat([ag.dists.features, gpd.GeoDataFrame(hub_features)], ignore_index=True)
ag.dists.features["geometry"] = ag.dists.features["geometry"].apply(lambda x: Point(x) if isinstance(x, list) else x)
ag.dists.features = gpd.GeoDataFrame(ag.dists.features, geometry="geometry")
ag.dists.features["centroid"] = gpd.GeoSeries(ag.dists.features["centroid"])

# Print the features with main_tag "hub"
hub_features_df = ag.dists.features[ag.dists.features["main_tag"] == "hub"]
print("Hub Features:")
print(hub_features_df.head())


Initializing data...
Loading geodata from geodata.pickle...
Loading graph from graph.pickle...
Loading features from features.pickle...


c:\Users\euseb\AppData\Local\Programs\Python\Python313\Lib\site-packages\geopandas\geodataframe.py:1819: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  super().__setitem__(key, value)
c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\eindhovenDists3.py:220: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  features["centroid"] = features.geometry.centroid
c:\Users\euseb\AppData\Local\Programs\Python\Python313\Lib\site-packages\geopandas\geodataframe.py:1819: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which 

Loading all pairs distances from all_pairs_distances.feather...


c:\Users\euseb\AppData\Local\Programs\Python\Python313\Lib\site-packages\geopandas\array.py:1638: UserWarning: CRS not set for some of the concatenation inputs. Setting output's CRS as WGS 84 (the single non-null crs provided).
  return GeometryArray(data, crs=_get_common_crs(to_concat))


Hub Features:
                       geometry addr:city addr:housenumber addr:postcode  \
51095   POINT (5.4786 51.44264)       NaN              NaN           NaN   
51096  POINT (5.47195 51.46464)       NaN              NaN           NaN   
51097  POINT (5.48933 51.45402)       NaN              NaN           NaN   
51098  POINT (5.47505 51.47604)       NaN              NaN           NaN   
51099   POINT (5.5202 51.43879)       NaN              NaN           NaN   

      addr:street brand brand:wikidata brand:wikipedia name opening_hours  \
51095         NaN   NaN            NaN             NaN  NaN           NaN   
51096         NaN   NaN            NaN             NaN  NaN           NaN   
51097         NaN   NaN            NaN             NaN  NaN           NaN   
51098         NaN   NaN            NaN             NaN  NaN           NaN   
51099         NaN   NaN            NaN             NaN  NaN           NaN   

       ... emergency ref:rce hoops sport_1 boules area main_tag  \

From here on out, we have all the data needed for developing a real-time simulation!

Let us first define some types of people (agents) that would live in Eindhoven

In [8]:
import random
seed = 42

universities = data["universities"]
offices = data["offices"]

# Function to create random Person objects
def create_person(residence_coords, type = 'child',  seed=42, walk_only=True, smart=False):

    random.seed(seed)

    nearest_node = ox.distance.nearest_nodes(
        graph, X=residence_coords[0], Y=residence_coords[1]
    )
    

    residence = ag.dists.get_nearest_amenities_from_node(
        graph, nearest_node, ('apartments', 'house'), 1
    )

    match type:
        case 'child':
            walk_speed = random.uniform(3, 5)
            bike_speed = random.uniform(6, 12)
            bike_freq = random.uniform(0.0, 0.8) if not walk_only else 0.0
            work_freq = 0.0
            features_freqs = {
                # According to statistics there are about 19k schoolchildren in eindhoven and 33k in ages 1-15
                # We can approximate the half of the rest going to kindergarten (even if it's not 100% accurate)
                ('school',) if random.random() < 0.8 else ('kindergarten',): 1.0,
                ('park', 'playground'): random.uniform(0.2, 0.9),
                ('pharmacy', 'hospital', 'clinic', 'doctors'): random.uniform(0.05, 0.2),
            }
            return ag.agent(
                    residence = residence,
                    work = None,
                    walk_speed=walk_speed,
                    bike_speed=bike_speed,
                    bike_freq=bike_freq,
                    work_freq=0.0,
                    features_freqs=features_freqs,
                    seed=seed,
                    smart=smart
                )
        case 'student':
            work = universities.sample(1)
            print(f"Selected university: {work}")
            walk_speed = random.uniform(3, 5)
            bike_speed = random.uniform(8, 20)
            bike_freq = random.uniform(0.0, 1.0) if not walk_only else 0.0
            work_freq = random.uniform(0.1, 0.9)
            features_freqs = {
                ('cafe', 'restaurant', 'bar', 'cinema', 'theatre'): random.uniform(0.2, 0.9),
                ('community_centre', 'library', 'bicycle_rental'): random.uniform(0.0, 0.3),
                ('park', 'fitness_centre', 'sports_centre', 'dog_park', 'pitch', 'swimming_pool'): random.uniform(0.1, 0.9),
                ('pharmacy', 'hospital', 'clinic', 'doctors'): random.uniform(0.0, 0.5),
                ('place_of_worship',): random.uniform(0.0, 0.5),
                ('supermarket', 'convenience', 'greengrocer', 'general'): random.uniform(0.2, 0.7),
                ('butcher', 'bakery', 'department_store', 'cosmetics', 'stationery'): random.uniform(0.0, 0.5),
                ('locker', 'parcel_locker'): random.uniform(0.5, 1.0)
            }

            return ag.agent(
                    residence=residence,
                    work=work,
                    walk_speed=walk_speed,
                    bike_speed=bike_speed,
                    bike_freq=bike_freq,
                    work_freq=work_freq,
                    features_freqs=features_freqs,
                    seed=seed,
                    smart=smart
                )
        case 'adult':
            work = offices.sample(1)
            print(f"Selected office: {work}")
            walk_speed = random.uniform(3, 5)
            bike_speed = random.uniform(8, 20)
            bike_freq = random.uniform(0.0, 1.0) if not walk_only else 0.0
            work_freq = random.uniform(0.8, 1.0)
            features_freqs = {
                ('cafe', 'restaurant', 'bar', 'cinema', 'theatre'): random.uniform(0.1, 0.7),
                ('community_centre', 'library', 'bicycle_rental'): random.uniform(0.0, 0.3),
                ('park', 'fitness_centre', 'sports_centre', 'dog_park', 'pitch', 'swimming_pool'): random.uniform(0.1, 0.9),
                ('pharmacy', 'hospital', 'clinic', 'doctors'): random.uniform(0.05, 0.2),
                ('place_of_worship',): random.uniform(0.0, 0.5),
                ('supermarket', 'convenience', 'greengrocer', 'general'): random.uniform(0.2, 0.7),
                ('butcher', 'bakery', 'department_store', 'cosmetics', 'stationery'): random.uniform(0.0, 0.5),
                ('locker', 'parcel_locker'): random.uniform(0.5, 1.0)
                }

            return ag.agent(
                    residence=residence,
                    work=work,
                    walk_speed=walk_speed,
                    bike_speed=bike_speed,
                    bike_freq=bike_freq,
                    work_freq=work_freq,
                    features_freqs=features_freqs,
                    seed=seed,
                    smart=smart
                )
        case 'senior':
            walk_speed = random.uniform(3, 5)
            bike_speed = random.uniform(8, 12)
            bike_freq = random.uniform(0.0, 1.0) if not walk_only else 0.0
            work_freq = 0.0
            features_freqs = {
                ('cafe', 'restaurant', 'bar', 'cinema', 'theatre'): random.uniform(0.25, 0.75),
                ('community_centre', 'library', 'bicycle_rental'): random.uniform(0.0, 0.75),
                ('park', 'fitness_centre', 'sports_centre', 'dog_park', 'pitch', 'swimming_pool'): random.uniform(0.1, 0.5),
                ('pharmacy', 'hospital', 'clinic', 'doctors'): random.uniform(0.1, 0.5),
                ('place_of_worship',): random.uniform(0.0, 0.5),
                ('supermarket', 'convenience', 'greengrocer', 'general'): random.uniform(0.2, 0.7),
                ('butcher', 'bakery', 'department_store', 'cosmetics', 'stationery'): random.uniform(0.0, 0.5),
                ('locker', 'parcel_locker'): random.uniform(0.5, 1.0),
            }

            return ag.agent(
                    residence=residence,
                    work=None,
                    walk_speed=walk_speed,
                    bike_speed=bike_speed,
                    bike_freq=bike_freq,
                    work_freq=work_freq,
                    features_freqs=features_freqs,
                    seed=seed,
                    smart=smart
                )

# Simulating

Now let us create an agent of type 'adult' and plot the different paths they take throughout two days, one using hubs, one without using hubs (we'll highlight the routes taken while walking in green and those taken while biking in orange)

In [9]:
# Create an agent and see the difference between simulate_day() and simulate_day_with_hubs()

residence_coords=(5.479767, 51.441985)
agent = create_person(
    residence_coords=residence_coords,  # Example coordinates
    type='adult',  # Change to 'child', 'student', 'adult', or 'senior' as needed
    seed=seed,
    walk_only=True,
    smart=False
)

nearest_node = ox.distance.nearest_nodes(
        graph, X=residence_coords[0], Y=residence_coords[1]
    )

nearest_amenities = ag.dists.get_nearest_amenities_from_node(
    graph, nearest_node, ('apartments', 'house'), 10)


bluenode = ag.dists.get_nearest_amenities_from_node(
    graph, nearest_node, ('house', 'apartments'), 2).iloc[0]['centroid']

print(ox.distance.nearest_nodes(ag.dists.data["graph"], X=agent.residence.geometry.centroid.x, Y=agent.residence.geometry.centroid.y))
# Highlight the residence on the map
eindhoven_map = folium.Map(location=[51.4416, 5.4697], zoom_start=12, tiles="cartodbpositron")
folium.CircleMarker(
    location=[agent.residence.geometry.centroid.y, agent.residence.geometry.centroid.x],
    radius=5,
    color="red",
    fill=True,
    fill_opacity=0.8,
    tooltip="Residence"
).add_to(eindhoven_map)
# Add the blue node (residence) to the map
folium.Marker(
    location=[bluenode.y, bluenode.x],
    icon=folium.Icon(color='blue', icon='home', prefix='fa'),
    tooltip="Residence Node"
).add_to(eindhoven_map)

# Add the mobility hubs to the map
for hub in hub_polygons:
    # Add a green circle marker for each hub centroid
    folium.CircleMarker(
        location=[hub.centroid.y, hub.centroid.x],
        radius=5,
        color="green",
        fill=True,
        fill_opacity=0.6,
        tooltip="Mobility Hub"
    ).add_to(eindhoven_map)
    

# Mark the nearest hub to the residence
nearest_hub = ag.dists.get_nearest_amenities_from_node(
    graph, nearest_node, ('hub',), 1).iloc[0]['centroid']

# Add a marker for the nearest hub
folium.Marker(
    location=[nearest_hub.y, nearest_hub.x],
    icon=folium.Icon(color='orange', icon='map-marker', prefix='fa'),
    tooltip="Nearest Hub"
).add_to(eindhoven_map)

# Simulate a day with the agent
results = agent.simulate_comparison()

# Print all feature ID's in df_travel
for index, row in agent.df_travel.iterrows():
    print(row)

# Map the routes between points travelled by the agent
for i in range(len(agent.df_travel) - 1):
    start = agent.df_travel.iloc[i]
    end = agent.df_travel.iloc[i + 1]

    # Color the route based on the mode of transport
    color = 'green' if start['mode'] == 'walk' else 'orange' if start['mode'] == 'bike' else 'blue'

    # Add a marker for the start point
    feature_start = ag.dists.features.iloc[start['feature_ID']]
    start_node = feature_start['nearest_node']

    feature_end = ag.dists.features.iloc[end['feature_ID']]
    end_node = feature_end['nearest_node']

    # Compute the shortest path between the start and end points
    route = ox.shortest_path(graph, start_node, end_node, weight='length')

    # Get the coordinates of the route
    route_coords = [(graph.nodes[node]['y'], graph.nodes[node]['x']) for node in route]
    # Add the route to the map
    folium.PolyLine(
        locations=route_coords,
        color=color,
        weight=2,
        opacity=0.6,
    ).add_to(eindhoven_map)


# Display the map with the residence highlighted
display(HTML(eindhoven_map._repr_html_()))

print(len(ag.dists.features[ag.dists.features['main_tag'].isin(('hub',))]))

if results:
    print(results['days_hubs'].head())
    print(results['days_nohubs'].head())



Number of amenities of type ('apartments', 'house') : 49802
Created BallTree for tags: ('apartments', 'house')
Selected office:                        geometry  addr:city addr:housenumber addr:postcode  \
31999  POINT (5.48097 51.45969)  Eindhoven               12        5623KK   

                  addr:street brand brand:wikidata brand:wikipedia    name  \
31999  Generaal Berenschotpad   NaN            NaN             NaN  Strang   

      opening_hours  ... building:flats emergency ref:rce hoops sport_1  \
31999           NaN  ...            NaN       NaN     NaN   NaN     NaN   

      boules area main_tag                  centroid nearest_node  
31999    NaN  NaN      yes  POINT (5.48097 51.45969)     42685915  

[1 rows x 216 columns]
Data already loaded.


C:\Users\euseb\AppData\Local\Temp\ipykernel_18068\3673248088.py:23: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  print(ox.distance.nearest_nodes(ag.dists.data["graph"], X=agent.residence.geometry.centroid.x, Y=agent.residence.geometry.centroid.y))
C:\Users\euseb\AppData\Local\Temp\ipykernel_18068\3673248088.py:27: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location=[agent.residence.geometry.centroid.y, agent.residence.geometry.centroid.x],
c:\Users\euseb\AppData\Local\Programs\Python\Python313\Lib\site-packages\folium\utilities.py:101: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  float(coord)
c:\Users\euseb

[61101653]
Number of amenities of type ('hub',) : 7
Created BallTree for tags: ('hub',)
Number of amenities of type ('dog_park', 'fitness_centre', 'park', 'pitch', 'sports_centre', 'swimming_pool') : 365
Created BallTree for tags: ('dog_park', 'fitness_centre', 'park', 'pitch', 'sports_centre', 'swimming_pool')
Day with hubs simulation complete.
Number of amenities of type ('locker', 'parcel_locker') : 18
Created BallTree for tags: ('locker', 'parcel_locker')
day                    0
travel_time     3.108931
mode                walk
amenity_type         hub
feature_ID         51095
Name: 0, dtype: object
day                                                             1
travel_time                                              3.052715
mode                                                         bike
amenity_type    (park, fitness_centre, sports_centre, dog_park...
feature_ID                                                  50159
Name: 1, dtype: object
day                     1
travel_ti

c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:315: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_hubs = pd.concat([df_travel_hubs, rows_hubs_travel], ignore_index=True)
c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:317: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_nohubs = pd.concat([df_travel_nohubs, rows_nohubs_travel], ignore_index=True)


7
   day  total_travel_time  work_travel_time
0  1.0          52.637569         18.574566
   day  total_travel_time  work_travel_time
0  2.0            92.9253         37.380493


Now we'll simulate a few days for agents covering our entire working area. We'll then average these days, comparing the travel times for the days wherein the agent walked to all their destination against those in which the agent took a detour to rent a bike and left it at a hub at the end of their day.

Below are the definitions for the different methods used to accomplish this.

In [10]:
import folium
import pandas as pd
from shapely.geometry import MultiPolygon
from concurrent.futures import ThreadPoolExecutor, as_completed

# We'll use the existing create_person function and grid_points list.
# We'll store travel times for each agent (with and without hubs).

def generateGridForMultiPolygon(multipolygon, spacing=0.006):
    points = []
    if isinstance(multipolygon, MultiPolygon):
        for poly in multipolygon.geoms:
            points.extend(generateGrid(poly, spacing))
    else:
        points = generateGrid(multipolygon, spacing)
    return points

grid_points = generateGridForMultiPolygon(data['geodata'])


def simulate_agent_days(pt, n_days=5, type='adult', seed=42):
    agent = create_person(
        residence_coords=(pt.x, pt.y),
        type=type,
        seed=seed,
        walk_only=True,
        smart=True
    )
    # Use the new simulate_comparison method
    results = agent.simulate_comparison(days=n_days, match_sampled_amenities=True) # Ensure we match sampled amenities
    # So the agent will do the exact same thing for each day, but with and without hubs.
    # Store the grid point and all result DataFrames
    return {
        'x': pt.x,
        'y': pt.y,
        'travel_hubs': results['travel_hubs'],
        'days_hubs': results['days_hubs'],
        'travel_nohubs': results['travel_nohubs'],
        'days_nohubs': results['days_nohubs']
    }

def run_simulation_for_type(type='adult', n_days=5):
    all_results = []
    with ThreadPoolExecutor() as executor:
        futures = [executor.submit(simulate_agent_days, pt, n_days, type) for pt in grid_points]
        for future in as_completed(futures):
            all_results.append(future.result())
    # Store results
    # all_agent_results is a list of dicts, each with x, y, and 4 DataFrames
    with pd.HDFStore(f"all_agent_simulation_results_{type}.h5", mode='w') as store:
        for i, result in enumerate(all_results):
            prefix = f"pt_{i}_x{result['x']:.5f}_y{result['y']:.5f}"
            # Add coordinates as columns to each DataFrame before saving
            for key in ['travel_hubs', 'days_hubs', 'travel_nohubs', 'days_nohubs']:
                df = result[key]
                df['grid_x'] = result['x']
                df['grid_y'] = result['y']
                store[f"{prefix}/{key}"] = df
                # For convenience, we'll still store the coordinates as metadata
                store.get_storer(f"{prefix}/{key}").attrs.grid_x = result['x']
                store.get_storer(f"{prefix}/{key}").attrs.grid_y = result['y']

    return all_results


def load_simulation_results(type='adult'):
    all_agent_results = []
    with pd.HDFStore(f"all_agent_simulation_results_{type}.h5", mode='r') as store:
        for key in store.keys():
            if key.startswith('/pt_') and key.endswith('/travel_hubs'):
                # Extract coordinates from the key
                parts = key.split('/')
                coords = parts[1].split('_')
                x = float(coords[2][1:])
                y = float(coords[3][1:])
                prefix = '/'.join(parts[:2])
                travel_hubs = store[f"{prefix}/travel_hubs"]
                days_hubs = store[f"{prefix}/days_hubs"]
                travel_nohubs = store[f"{prefix}/travel_nohubs"]
                days_nohubs = store[f"{prefix}/days_nohubs"]
                all_agent_results.append({
                    'x': x,
                    'y': y,
                    'travel_hubs': travel_hubs,
                    'days_hubs': days_hubs,
                    'travel_nohubs': travel_nohubs,
                    'days_nohubs': days_nohubs
                })
    return all_agent_results

# Process results to create a DataFrame for travel times
def process_simulation_results(results):
    summary = []
    for result in results:
        # Only process entries that are dicts and have the expected DataFrames
        if not isinstance(result, dict):
            continue
        # Check for required keys and DataFrame types
        required_keys = ['days_nohubs', 'days_hubs', 'x', 'y']
        if not all(k in result for k in required_keys):
            continue
        if not (isinstance(result['days_nohubs'], pd.DataFrame) and isinstance(result['days_hubs'], pd.DataFrame)):
            continue

        avg_no_hub = result['days_nohubs']['total_travel_time'].mean() if not result['days_nohubs'].empty else None
        avg_with_hub = result['days_hubs']['total_travel_time'].mean() if not result['days_hubs'].empty else None
        summary.append({
            'x': result['x'],
            'y': result['y'],
            'time_no_hub': avg_no_hub,
            'time_with_hub': avg_with_hub
        })
    return pd.DataFrame(summary)


# Normalize travel times for color mapping
def get_color(val, vmin, vmax):
    # Green = fast, Red = slow
    if val is None:
        return 'gray'
    ratio = (val - vmin) / (vmax - vmin) if vmax > vmin else 0
    r = int(255 * ratio)
    g = int(255 * (1 - ratio))
    return f'#{r:02x}{g:02x}00'


def create_map(travel_times_df, hub_polygons):

    # Compute min/max for color scaling
    valid_no_hub = travel_times_df['time_no_hub'].dropna()
    valid_with_hub = travel_times_df['time_with_hub'].dropna()
    min_time = min(valid_no_hub.min(), valid_with_hub.min())
    max_time = max(valid_no_hub.max(), valid_with_hub.max())

    # Create a Folium map centered around Eindhoven
    travel_map = folium.Map(location=[51.4416, 5.4697], zoom_start=12, tiles="cartodbpositron")

    # Add points for travel time without hubs (circle)
    for _, row in travel_times_df.iterrows():
        color = get_color(row['time_no_hub'], min_time, max_time)
        folium.CircleMarker(
            location=[row['y'], row['x']],
            radius=10,
            color=color,
            fill=True,
            fill_opacity=0.7,
            tooltip=f"No hub: {row['time_no_hub']:.1f} min" if row['time_no_hub'] is not None else "No data"
        ).add_to(travel_map)

    # Add points for travel time with hubs (square marker)
    for _, row in travel_times_df.iterrows():
        color = get_color(row['time_with_hub'], min_time, max_time)
        folium.RegularPolygonMarker(
            location=[row['y'], row['x']],
            number_of_sides=4,
            radius=5,
            color=color,
            fill=True,
            fill_opacity=0.5,
            tooltip=f"With hub: {row['time_with_hub']:.1f} min" if row['time_with_hub'] is not None else "No data"
        ).add_to(travel_map)

    # Add the hub locations to the map
    for poly in hub_polygons:
        folium.Polygon(
            locations=[(pt[1], pt[0]) for pt in poly.exterior.coords],
            color='red', weight=2, fill=True, fill_opacity=0.3
        ).add_to(travel_map)

    # Add a legend
    legend_html = """
    <div style="position: fixed; 
        bottom: 50px; left: 50px; width: 200px; height: 90px; 
        background-color: white; z-index:9999; font-size:14px;
        border:2px solid grey; border-radius:8px; padding: 10px;">
    <b>Travel Time Legend</b><br>
    <span style="color:#00ff00;">&#9632;</span> Fast (min)<br>
    <span style="color:#ff0000;">&#9632;</span> Slow (max)<br>
    Circle: No hub<br>
    Diamond: With hub
    </div>
    """
    travel_map.get_root().html.add_child(folium.Element(legend_html))

    return travel_map

### Running the simulation

Now we will run our simulation for different kinds of agents. We will consider the ones we outlined as our target audiences.

In [11]:
# Run the simulation for the different types of agents
agent_types = ['student', 'adult', 'senior']
all_agent_results = {}
""" # <- To uncomment, add another set of triple quotes here
# Uncomment this block to run the simulation for all agent types
for agent_type in agent_types:
    print(f"Running simulation for {agent_type} agents...")
    all_agent_results[agent_type] = run_simulation_for_type(type=agent_type, n_days=5)
""" """"""

' # <- To uncomment, add another set of triple quotes here\n# Uncomment this block to run the simulation for all agent types\nfor agent_type in agent_types:\n    print(f"Running simulation for {agent_type} agents...")\n    all_agent_results[agent_type] = run_simulation_for_type(type=agent_type, n_days=5)\n'

In [12]:
import pandas as pd


def summarize_improvements(results):
    summary_rows = []
    for agent_type, results in results.items():

        df = process_simulation_results(results)
        
        # Drop rows with missing data
        df = df.dropna(subset=['time_no_hub', 'time_with_hub'])
        if df.empty:
            print(f"No data for {agent_type}")
            continue

        avg_no_hub = df['time_no_hub'].mean()
        avg_with_hub = df['time_with_hub'].mean()
        median_no_hub = df['time_no_hub'].median()
        median_with_hub = df['time_with_hub'].median()
        min_no_hub = df['time_no_hub'].min()
        min_with_hub = df['time_with_hub'].min()
        max_no_hub = df['time_no_hub'].max()
        max_with_hub = df['time_with_hub'].max()
        improvement = avg_no_hub - avg_with_hub
        percent_improved = (df['time_no_hub'] > df['time_with_hub']).mean() * 100

        print(f"\n=== {agent_type.capitalize()} Agents ===")
        print(f"Average travel time without hubs: {avg_no_hub:.2f} min")
        print(f"Average travel time with hubs:    {avg_with_hub:.2f} min")
        print(f"Median travel time without hubs:  {median_no_hub:.2f} min")
        print(f"Median travel time with hubs:     {median_with_hub:.2f} min")
        print(f"Min travel time without hubs:     {min_no_hub:.2f} min")
        print(f"Min travel time with hubs:        {min_with_hub:.2f} min")
        print(f"Max travel time without hubs:     {max_no_hub:.2f} min")
        print(f"Max travel time with hubs:        {max_with_hub:.2f} min")
        print(f"Average improvement:              {improvement:.2f} min")
        print(f"Percentage of agents improved:    {percent_improved:.1f}%")

        summary_rows.append({
            'Agent Type': agent_type,
            'Avg No Hub': avg_no_hub,
            'Avg With Hub': avg_with_hub,
            'Median No Hub': median_no_hub,
            'Median With Hub': median_with_hub,
            'Avg Improvement': improvement,
            '% Improved': percent_improved
        })

    # Summary table
    summary_df = pd.DataFrame(summary_rows)
    print("\n=== Summary Table ===")
    print(summary_df)

# Call the function after running all simulations
# Load the results for each agent type
# Load results for each agent type
# Can be uncommented to skip running the simulation again
for agent_type in agent_types: all_agent_results[agent_type] = load_simulation_results(type=agent_type)
summarize_improvements(all_agent_results)

# results_student = all_agent_results['student']

# print(results_student[0]['days_hubs'].head())


=== Student Agents ===
Average travel time without hubs: 83.18 min
Average travel time with hubs:    101.87 min
Median travel time without hubs:  72.26 min
Median travel time with hubs:     95.59 min
Min travel time without hubs:     5.16 min
Min travel time with hubs:        27.12 min
Max travel time without hubs:     304.61 min
Max travel time with hubs:        315.23 min
Average improvement:              -18.69 min
Percentage of agents improved:    39.8%

=== Adult Agents ===
Average travel time without hubs: 128.38 min
Average travel time with hubs:    116.48 min
Median travel time without hubs:  126.86 min
Median travel time with hubs:     111.90 min
Min travel time without hubs:     15.37 min
Min travel time with hubs:        22.51 min
Max travel time without hubs:     268.85 min
Max travel time with hubs:        310.19 min
Average improvement:              11.90 min
Percentage of agents improved:    59.2%

=== Senior Agents ===
Average travel time without hubs: 11.12 min
Averag

In [13]:
extra_tags = ['locker', 'parcel_locker', 'public_bathroom', 'public_toilet']
# This will be relevant for simulating the accessibility of hubs with additional features.
def create_extra_tags_features(hubs, tags):
    extra_features = []
    for i, hub in enumerate(hubs):
        nearest_node = ox.distance.nearest_nodes(graph, hub.centroid.x, hub.centroid.y)
        centroid = hub.centroid
        for tag in tags:
            extra_features.append({
                "id": f"{tag}_{i}",
                "geometry": centroid,
                "main_tag": tag,
                "centroid": centroid,
                "nearest_node": nearest_node
            })
    return extra_features

# 1. Run the first simulation (baseline)
results_baseline = {}
for agent_type in agent_types:
    print(f"Running baseline simulation for {agent_type} agents...")
    results_baseline[agent_type] = run_simulation_for_type(type=agent_type, n_days=5)

# 2. Add extra features (lockers, parcel lockers, public bathrooms, public toilets)
extra_tags = ['locker', 'parcel_locker', 'public_bathroom', 'public_toilet']
extra_features = create_hub_features(hub_polygons)  # This now includes extra features

# Add extra features to ag.dists.features
ag.dists.features = pd.concat([ag.dists.features, gpd.GeoDataFrame(extra_features)], ignore_index=True)
ag.dists.features["geometry"] = ag.dists.features["geometry"].map(lambda x: Point(x) if isinstance(x, list) else x)
ag.dists.features = gpd.GeoDataFrame(ag.dists.features, geometry="geometry")
ag.dists.features["centroid"] = gpd.GeoSeries(ag.dists.features["centroid"])

# 3. Run the second simulation (with extra features)
results_with_extras = {}
for agent_type in agent_types:
    print(f"Running simulation with extra features for {agent_type} agents...")
    results_with_extras[agent_type] = run_simulation_for_type(type=agent_type, n_days=5)




Running baseline simulation for student agents...
Selected university:                       geometry  addr:city addr:housenumber addr:postcode  \
32009  POINT (5.47584 51.4564)  Eindhoven                1        5623AD   

      addr:street brand brand:wikidata brand:wikipedia            name  \
32009  Kaakstraat   NaN            NaN             NaN  De Rooi Pannen   

      opening_hours  ... building:flats emergency ref:rce hoops sport_1  \
32009           NaN  ...            NaN       NaN     NaN   NaN     NaN   

      boules area main_tag                 centroid nearest_node  
32009    NaN  NaN  college  POINT (5.47584 51.4564)   8615238354  

[1 rows x 216 columns]
Data already loaded.
Selected university:                       geometry  addr:city addr:housenumber addr:postcode  \
32009  POINT (5.47584 51.4564)  Eindhoven                1        5623AD   

      addr:street brand brand:wikidata brand:wikipedia            name  \
32009  Kaakstraat   NaN            NaN           

c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:315: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_hubs = pd.concat([df_travel_hubs, rows_hubs_travel], ignore_index=True)
c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:315: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_hubs = pd.concat([df_travel_hubs, rows_hubs_travel], ignore_index=True)
c:\Users\euseb\OneDrive - TU

Day with hubs simulation complete.
Number of amenities of type ('bar', 'cafe', 'cinema', 'restaurant', 'theatre') : 362
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Created BallTree for tags: ('bar', 'cafe', 'cinema', 'restaurant', 'theatre')
Created BallTree for tags: ('bar', 'cafe', 'cinema', 'restaurant', 'theatre')
Number of amenities of type ('bar', 'cafe', 'cinema', 'restaurant', 'theatre') : 362
Day with hubs simulation complete.
Day with hubs simulation complete.


c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:315: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_hubs = pd.concat([df_travel_hubs, rows_hubs_travel], ignore_index=True)
c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:317: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_nohubs = pd.concat([df_travel_nohubs, rows_nohubs_travel], ignore_index=True)
c:\Users\euseb\OneDriv

Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Number of amenities of type ('clinic', 'doctors', 'hospital', 'pharmacy') : 38
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Created BallTree for tags: ('bar', 'cafe', 'cinema', 'restaurant', 'theatre')
Day with hubs simulation complete.
Created BallTree for tags: ('clinic', 'doctors', 'hospital', 'pharmacy')
Day with hubs simulation complete.


...

c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:315: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_hubs = pd.concat([df_travel_hubs, rows_hubs_travel], ignore_index=True)
c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:317: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_nohubs = pd.concat([df_travel_nohubs, rows_nohubs_travel], ignore_index=True)
c:\Users\euseb\OneDriv

Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.Day with hubs simulation complete.

Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Data already loaded.
Data already loaded.
Data already loaded.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation co

c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:315: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_hubs = pd.concat([df_travel_hubs, rows_hubs_travel], ignore_index=True)
c:\Users\euseb\OneDrive - TU Eindhoven\Documents\GitHub\Project-4CBLW00-17\ImprovedSimulation\agent.py:315: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_travel_hubs = pd.concat([df_travel_hubs, rows_hubs_travel], ignore_index=True)
c:\Users\euseb\OneDrive - TU

Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.Day with hubs simulation complete.

Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.
Day with hubs simulation complete.


c:\Users\euseb\AppData\Local\Programs\Python\Python313\Lib\site-packages\tables\path.py:146: NaturalNameWarning: object name is not a valid Python identifier: 'pt_0_x5.47391_y51.41504'; it does not match the pattern ``^[a-zA-Z_][a-zA-Z0-9_]*$``; you will not be able to use natural naming to access this object; using ``getattr()`` will still work, though
  check_attribute_name(name)
C:\Users\euseb\AppData\Local\Temp\ipykernel_18068\655822240.py:58: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed-integer,key->block1_values] [items->Index(['day', 'mode', 'amenity_type', 'feature_ID'], dtype='object')]

  store[f"{prefix}/{key}"] = df
C:\Users\euseb\AppData\Local\Temp\ipykernel_18068\655822240.py:58: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed-integer,key->block1_values] [items->Index(['day'

In [16]:
# 4. Summarize improvements
summarize_improvements(results_baseline)
summarize_improvements(results_with_extras)




=== Student Agents ===
Average travel time without hubs: 66.73 min
Average travel time with hubs:    98.41 min
Median travel time without hubs:  54.23 min
Median travel time with hubs:     95.72 min
Min travel time without hubs:     2.60 min
Min travel time with hubs:        19.94 min
Max travel time without hubs:     202.27 min
Max travel time with hubs:        269.35 min
Average improvement:              -31.68 min
Percentage of agents improved:    28.2%

=== Adult Agents ===
Average travel time without hubs: 118.67 min
Average travel time with hubs:    113.55 min
Median travel time without hubs:  109.03 min
Median travel time with hubs:     104.00 min
Min travel time without hubs:     16.83 min
Min travel time with hubs:        18.47 min
Max travel time without hubs:     318.72 min
Max travel time with hubs:        263.56 min
Average improvement:              5.13 min
Percentage of agents improved:    49.5%

=== Senior Agents ===
Average travel time without hubs: 11.25 min
Average 